# 앞 뒤 predict growth가 같지만, 중간만 다른 경우 매핑

- mask_id별로 반복
- iterrows() 로 idx도 같이 뽑아서 iloc으로 값 바꾸기

In [1]:
import pandas as pd

data_path = "/home/ubuntu/drive/preprocessing/merged_growth_real_final_filtering2.csv"
data = pd.read_csv(data_path)

In [25]:
data = data[data["is_filtering"] < 1]

In [67]:
data.drop("Unnamed: 0", axis=1, inplace=True)

In [26]:
data.info()
data.head(3)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 127857 entries, 0 to 127856
Data columns (total 35 columns):
 #   Column               Non-Null Count   Dtype         
---  ------               --------------   -----         
 0   Unnamed: 0           127857 non-null  int64         
 1   check_datetime       127857 non-null  datetime64[ns]
 2   측정일자                 127857 non-null  object        
 3   구역명                  127857 non-null  object        
 4   farm_code            127857 non-null  object        
 5   내부온도                 126222 non-null  float64       
 6   내부습도                 126222 non-null  float64       
 7   내부CO2                126222 non-null  float64       
 8   근권온도                 126222 non-null  float64       
 9   내부순간일사량              126222 non-null  float64       
 10  측정년도                 127857 non-null  int64         
 11  측정월                  127857 non-null  int64         
 12  input_image_name     127857 non-null  object        
 13  input_image_pa

Unnamed: 0      check_datetime        측정일자  구역명 farm_code   내부온도   내부습도  \
0       48922 2021-12-11 12:30:00  2021-12-11  1구역     F0017  21.10  84.80   
1       55848 2022-01-12 08:30:00  2022-01-12  1구역     F0017  10.41  91.72   
2       56018 2022-01-12 16:50:00  2022-01-12  1구역     F0017  15.14  85.69   

    내부CO2   근권온도  내부순간일사량  ...    size  \
0   407.3  14.90   112.85  ...  1509.0   
1  2812.2  12.76    14.66  ...  1446.0   
2   281.7  14.05    21.42  ...  1183.0   

                                               color  output_image_path  \
0  [[62, 75, 45], [95, 108, 78], [87, 100, 70], [...  image_mask_17.png   
1  [[38, 54, 15], [63, 78, 39], [55, 70, 29], [47...  image_mask_13.png   
2  [[57, 68, 36], [57, 66, 35], [40, 49, 18], [29...  image_mask_13.png   

   origin_r  origin_g  origin_b pred_growth  mask_count is_filtering  \
0  0.350209  0.414472  0.235319      unripe        48.0          0.0   
1  0.379927  0.409472  0.210601      unripe        91.0          0.0   
2  0.380081  0.397676  0.222243      unripe        87.0          0.0   

  preprocessed_growth  
0              unripe  
1              unripe  
2              unripe  

[3 rows x 35 columns]

In [4]:
# 정렬을 위해 check_datetime 타입 변경
data["check_datetime"] = pd.to_datetime(data["check_datetime"])

In [27]:
data["preprocessed_growth"] = data["pred_growth"]

In [28]:
### 앞뒤가 같은데 현재가 다를 경우 현재 생육 단계 수정

# mask_id 기준, check_datetime 기준 정렬 후 인덱스 초기화
data.sort_values(by=["mask_id", "check_datetime"], inplace=True, ignore_index=True)

# growth = data[["check_datetime", "mask_id", "pred_growth", "preprocessed_growth"]]

# mask_id 단위로 반복
for i, mask_id in enumerate(data["mask_id"].unique()):
    # 예측값 idx, values 형태로 가져오기
    print(f"<{i}번째 mask_id : {mask_id}>")
    preds_keys = data[data["mask_id"] == mask_id]["preprocessed_growth"][1:-1].keys()
    # 반복하며 앞뒤 확인
    for idx in preds_keys:
        preds = data[data["mask_id"] == mask_id]["preprocessed_growth"]
        # 앞 뒤가 같고, 중간은 다른 경우 매핑
        if preds[idx-1] == preds[idx+1] and preds[idx-1] != preds[idx]:
            data.loc[idx, "preprocessed_growth"] = preds[idx-1]

<0번째 mask_id : 000e746a20045adde95ecafc59ac8162_0>
<1번째 mask_id : 000e746a20045adde95ecafc59ac8162_1>
<2번째 mask_id : 000e746a20045adde95ecafc59ac8162_2>
<3번째 mask_id : 000e746a20045adde95ecafc59ac8162_3>
<4번째 mask_id : 000e746a20045adde95ecafc59ac8162_4>
<5번째 mask_id : 000e746a20045adde95ecafc59ac8162_5>
<6번째 mask_id : 000e746a20045adde95ecafc59ac8162_6>
<7번째 mask_id : 000e746a20045adde95ecafc59ac8162_7>
<8번째 mask_id : 001417bcc9ecfe8a4b53b14030ac70be_0>
<9번째 mask_id : 001417bcc9ecfe8a4b53b14030ac70be_1>
<10번째 mask_id : 001417bcc9ecfe8a4b53b14030ac70be_2>
<11번째 mask_id : 001417bcc9ecfe8a4b53b14030ac70be_3>
<12번째 mask_id : 001417bcc9ecfe8a4b53b14030ac70be_4>
<13번째 mask_id : 00198d750efd3dcbbcc79da2db2907c5_0>
<14번째 mask_id : 002330f7b790f7473817e2f46cbf06f8_0>
<15번째 mask_id : 002330f7b790f7473817e2f46cbf06f8_1>
<16번째 mask_id : 002330f7b790f7473817e2f46cbf06f8_2>
<17번째 mask_id : 002330f7b790f7473817e2f46cbf06f8_3>
<18번째 mask_id : 002330f7b790f7473817e2f46cbf06f8_4>
<19번째 mask_id : 002399

In [ ]:
### 앞뒤가 같은데 현재가 다를 경우 현재 생육 단계 수정
## grwoth로 빼서 동작하는 경우

# mask_id 기준, check_datetime 기준 정렬 후 인덱스 초기화
# data.sort_values(by=["mask_id", "check_datetime"], inplace=True, ignore_index=True)

# growth = data[["check_datetime", "mask_id", "pred_growth", "preprocessed_growth"]]

# # mask_id 단위로 반복
# for i, mask_id in enumerate(growth["mask_id"].unique()):
#     # 예측값 idx, values 형태로 가져오기
#     print(f"<{i}번째 mask_id : {mask_id}>")
#     preds_keys = growth[growth["mask_id"] == mask_id]["preprocessed_growth"][1:-1].keys()
#     # 반복하며 앞뒤 확인
#     for idx in preds_keys:
#         preds = growth[growth["mask_id"] == mask_id]["preprocessed_growth"]
#         # 앞 뒤가 같고, 중간은 다른 경우 매핑
#         if preds[idx-1] == preds[idx+1] and preds[idx-1] != preds[idx]:
#             growth.loc[idx, "preprocessed_growth"] = preds[idx-1]

In [29]:
# 달라진 경우
data[data["pred_growth"] != data["preprocessed_growth"]][data["pred_growth"].notna()][["pred_growth", "preprocessed_growth"]]

/tmp/ipykernel_10167/4077469868.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  data[data["pred_growth"] != data["preprocessed_growth"]][data["pred_growth"].notna()][["pred_growth", "preprocessed_growth"]]


pred_growth preprocessed_growth
20       semi-ripe                ripe
55            ripe           semi-ripe
74            ripe           semi-ripe
112      semi-ripe                ripe
191      semi-ripe              unripe
...            ...                 ...
127710        ripe           semi-ripe
127744        ripe           semi-ripe
127811   semi-ripe                ripe
127814   semi-ripe                ripe
127845        ripe           semi-ripe

[4658 rows x 2 columns]

중간저장

In [ ]:
data.to_csv("./merge_drowth_real_final_filtering3.csv", index=False, encoding="utf8")

---

# 극단적으로 생육 단계가 바뀐 경우 mask_id 나누기

In [30]:
import pandas as pd

data = pd.read_csv("merged_growth_real_final_filtering3.csv")

In [31]:
data["check_datetime"] = pd.to_datetime(data["check_datetime"])
data.sort_values(by=["mask_id", "check_datetime"], inplace=True, ignore_index=True)

In [32]:
data["is_ripe_to_unripe"] = 0

In [4]:
data.iloc[:4, 30:]

origin_g  origin_b pred_growth  mask_count  is_filtering  \
0  0.414472  0.235319      unripe        48.0           0.0   
1  0.409472  0.210601      unripe        91.0           0.0   
2  0.397676  0.222243      unripe        87.0           0.0   
3  0.404960  0.202923      unripe        92.0           0.0   

  preprocessed_growth  is_ripe_to_unripe  
0              unripe                  0  
1              unripe                  0  
2              unripe                  0  
3              unripe                  0

In [33]:
### 다음날이지만 극단적으로 변한 경우 ripe -> unripe, mask_id 나누기
# mask_id별로 순회 -> 극단적으로 변하면 변한 시점부터 끝까지 새로운 mask_id를 부여
# 그런데 새로 부여된 mask_id 안에서도 그런 경우가 존재할 수 있다.
# mask_id로 돌면서 극단적으로 변한 경우 ripe_to_unripe 컬럼에 1 값을 넣어두고, 나중에는 이 1 값이 있는 인덱스를 iterable 형태로 불러온다.
# iterable을 돌면서 .iloc[idx: idx+1] 인 경우의 mask_id를 새롭게 정의해주면 되지 않을지..

## ripe to unripe 확인
# mask_id 단위로 반복
for i, mask_id in enumerate(data["mask_id"].unique()):
    # 예측값 idx, values 형태로 가져오기
    print(f"<{i}번째 mask_id : {mask_id}>")
    preds_keys = data[data["mask_id"] == mask_id]["preprocessed_growth"][1:].keys()
    # 반복하며 이전 growth와 비교
    for idx in preds_keys:
        preds = data[data["mask_id"] == mask_id]["preprocessed_growth"]
        # 앞 뒤가 같고, 중간은 다른 경우 매핑
        if preds[idx-1] == "ripe" and preds[idx] == "unripe":
            data.loc[idx, "is_ripe_to_unripe"] = 1

<0번째 mask_id : 000e746a20045adde95ecafc59ac8162_0>
<1번째 mask_id : 000e746a20045adde95ecafc59ac8162_1>
<2번째 mask_id : 000e746a20045adde95ecafc59ac8162_2>
<3번째 mask_id : 000e746a20045adde95ecafc59ac8162_3>
<4번째 mask_id : 000e746a20045adde95ecafc59ac8162_4>
<5번째 mask_id : 000e746a20045adde95ecafc59ac8162_5>
<6번째 mask_id : 000e746a20045adde95ecafc59ac8162_6>
<7번째 mask_id : 000e746a20045adde95ecafc59ac8162_7>
<8번째 mask_id : 001417bcc9ecfe8a4b53b14030ac70be_0>
<9번째 mask_id : 001417bcc9ecfe8a4b53b14030ac70be_1>
<10번째 mask_id : 001417bcc9ecfe8a4b53b14030ac70be_2>
<11번째 mask_id : 001417bcc9ecfe8a4b53b14030ac70be_3>
<12번째 mask_id : 001417bcc9ecfe8a4b53b14030ac70be_4>
<13번째 mask_id : 00198d750efd3dcbbcc79da2db2907c5_0>
<14번째 mask_id : 002330f7b790f7473817e2f46cbf06f8_0>
<15번째 mask_id : 002330f7b790f7473817e2f46cbf06f8_1>
<16번째 mask_id : 002330f7b790f7473817e2f46cbf06f8_2>
<17번째 mask_id : 002330f7b790f7473817e2f46cbf06f8_3>
<18번째 mask_id : 002330f7b790f7473817e2f46cbf06f8_4>
<19번째 mask_id : 002399

In [41]:
data_check = data[["check_datetime", "mask_id", "pred_growth", "preprocessed_growth", "is_ripe_to_unripe"]]

In [42]:
data_check[data_check["mask_id"] == "e801a194cac949d955eedc5052e03832_0"]

check_datetime                             mask_id pred_growth  \
115718 2022-01-27 08:40:00  e801a194cac949d955eedc5052e03832_0      unripe   
115719 2022-01-28 08:30:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115720 2022-01-28 12:30:00  e801a194cac949d955eedc5052e03832_0        ripe   
115721 2022-01-28 17:00:00  e801a194cac949d955eedc5052e03832_0        ripe   
115722 2022-01-29 08:50:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115723 2022-01-29 12:30:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115724 2022-01-29 16:40:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115725 2022-01-30 08:30:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115726 2022-01-30 12:30:00  e801a194cac949d955eedc5052e03832_0        ripe   
115727 2022-01-31 08:30:00  e801a194cac949d955eedc5052e03832_0      unripe   
115728 2022-01-31 12:30:00  e801a194cac949d955eedc5052e03832_0      unripe   
115729 2022-01-31 16:40:00  e801a194cac949d955eedc5052e03832_0      unripe   
115730 2022-02-01 12:30:00  e801a194cac949d955eedc5052e03832_0      unripe   
115731 2022-02-01 16:30:00  e801a194cac949d955eedc5052e03832_0      unripe   
115732 2022-02-02 08:40:00  e801a194cac949d955eedc5052e03832_0      unripe   
115733 2022-02-02 12:30:00  e801a194cac949d955eedc5052e03832_0      unripe   
115734 2022-02-02 16:40:00  e801a194cac949d955eedc5052e03832_0      unripe   
115735 2022-02-03 08:30:00  e801a194cac949d955eedc5052e03832_0      unripe   
115736 2022-02-03 16:30:00  e801a194cac949d955eedc5052e03832_0      unripe   
115737 2022-02-04 09:00:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115738 2022-02-04 16:30:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115739 2022-02-05 12:30:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115740 2022-02-06 12:30:00  e801a194cac949d955eedc5052e03832_0        ripe   

       preprocessed_growth  is_ripe_to_unripe  
115718              unripe                  0  
115719           semi-ripe                  0  
115720                ripe                  0  
115721                ripe                  0  
115722           semi-ripe                  0  
115723           semi-ripe                  0  
115724           semi-ripe                  0  
115725           semi-ripe                  0  
115726                ripe                  0  
115727              unripe                  1  
115728              unripe                  0  
115729              unripe                  0  
115730              unripe                  0  
115731              unripe                  0  
115732              unripe                  0  
115733              unripe                  0  
115734              unripe                  0  
115735              unripe                  0  
115736              unripe                  0  
115737           semi-ripe                  0  
115738           semi-ripe                  0  
115739           semi-ripe                  0  
115740                ripe                  0

주의!!!! loc은 리스트 인덱싱과 다르게 A ~ B로 하면 B까지 나온다. B-1까지 나오지 않음

In [57]:
## mask_id별 체크한 것에 기반해서 mask_id 부여하기
# mask_id에 indexes를 순회하면서 알 수 있는 i를 추가로 붙여줌

res_data = data.copy()

mask_ids = res_data[res_data["is_ripe_to_unripe"] > 0]["mask_id"].values

for mask_id in mask_ids:
    print(f"mask_id : {mask_id}")
    # 값이 1인 경우(바뀐 경우) 인덱스만 가져오기 (+mask_id의 마지막 인덱스)
    indexes = res_data[(res_data["mask_id"] == mask_id) & res_data["is_ripe_to_unripe"] > 0].index
    indexes = indexes.append(res_data[res_data["mask_id"] == mask_id].index[-1:])
    print(indexes)
    # 1인 경우 
    for i, v in enumerate(indexes[:-1]):
        res_data.loc[v:indexes[i+1], "mask_id"] = f"{mask_id}_{i}"

mask_id : 001417bcc9ecfe8a4b53b14030ac70be_4
Index([58, 70], dtype='int64')
mask_id : 00715d5ec46b3d94a8ee5e41cf21613e_2
Index([264, 267], dtype='int64')
mask_id : 00c62e145740fc1bcc6cc43dc6c08832_0
Index([551, 553], dtype='int64')
mask_id : 0101823eb058f89d3008585f28658a94_2
Index([643, 664], dtype='int64')
mask_id : 0101823eb058f89d3008585f28658a94_4
Index([677, 689], dtype='int64')
mask_id : 03311a5c92cdcd7f791a5d21776ae93d_4
Index([1689, 1689], dtype='int64')
mask_id : 034077223285cfc7af419ae0733e116c_6
Index([1770, 1771], dtype='int64')
mask_id : 03b1b4316ddbf4bba3ba8e8b0c2715ea_4
Index([1953, 1955], dtype='int64')
mask_id : 04d7d2f009f6985365664da49df31867_0
Index([2493, 2493], dtype='int64')
mask_id : 067a480b75ed924d81d916362997bbfa_11
Index([3189, 3190], dtype='int64')
mask_id : 07b9ba11a40b64b82c56b8185b4d3e59_2
Index([3802, 3811], dtype='int64')
mask_id : 07cb6314ab36183d8ff683a135d5790d_1
Index([3887, 3907], dtype='int64')
mask_id : 098f6ae056e37b6a678b7909d210569b_2
Index(

In [58]:
data_check = res_data[["check_datetime", "mask_id", "pred_growth", "preprocessed_growth", "is_ripe_to_unripe"]]

In [59]:
data_check[data_check["mask_id"] == "e801a194cac949d955eedc5052e03832_0"]

check_datetime                             mask_id pred_growth  \
115718 2022-01-27 08:40:00  e801a194cac949d955eedc5052e03832_0      unripe   
115719 2022-01-28 08:30:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115720 2022-01-28 12:30:00  e801a194cac949d955eedc5052e03832_0        ripe   
115721 2022-01-28 17:00:00  e801a194cac949d955eedc5052e03832_0        ripe   
115722 2022-01-29 08:50:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115723 2022-01-29 12:30:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115724 2022-01-29 16:40:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115725 2022-01-30 08:30:00  e801a194cac949d955eedc5052e03832_0   semi-ripe   
115726 2022-01-30 12:30:00  e801a194cac949d955eedc5052e03832_0        ripe   

       preprocessed_growth  is_ripe_to_unripe  
115718              unripe                  0  
115719           semi-ripe                  0  
115720                ripe                  0  
115721                ripe                  0  
115722           semi-ripe                  0  
115723           semi-ripe                  0  
115724           semi-ripe                  0  
115725           semi-ripe                  0  
115726                ripe                  0

In [60]:
data_check.iloc[115724:115730]

check_datetime                               mask_id pred_growth  \
115724 2022-01-29 16:40:00    e801a194cac949d955eedc5052e03832_0   semi-ripe   
115725 2022-01-30 08:30:00    e801a194cac949d955eedc5052e03832_0   semi-ripe   
115726 2022-01-30 12:30:00    e801a194cac949d955eedc5052e03832_0        ripe   
115727 2022-01-31 08:30:00  e801a194cac949d955eedc5052e03832_0_0      unripe   
115728 2022-01-31 12:30:00  e801a194cac949d955eedc5052e03832_0_0      unripe   
115729 2022-01-31 16:40:00  e801a194cac949d955eedc5052e03832_0_0      unripe   

       preprocessed_growth  is_ripe_to_unripe  
115724           semi-ripe                  0  
115725           semi-ripe                  0  
115726                ripe                  0  
115727              unripe                  1  
115728              unripe                  0  
115729              unripe                  0

In [11]:
# 정렬 
# data.sort_values(by=["farm_code", "check_datetime"], inplace=True)
# data.to_csv("/home/ubuntu/drive/preprocessing/preprocessed_merged_data.csv")

In [62]:
# 중간 저장
res_data.sort_values(by=["farm_code", "check_datetime"], inplace=True)
res_data.to_csv("./merge_drowth_real_final_filtering4.csv", index=False, encoding="utf8")

---

# 맨 마지막 딸기만 갑자기 단계가 낮아지는 경우 수정

In [104]:
data = pd.read_csv("merge_drowth_real_final_filtering4.csv")

In [107]:
res_data = data.copy()

In [108]:
data_check = res_data[["check_datetime", "mask_id", "pred_growth", "preprocessed_growth", "is_ripe_to_unripe"]]
data_check[data_check["mask_id"] == "f4a0c6e25664af6ed0f03228fb2c9bf3_1"]

check_datetime                             mask_id pred_growth  \
25783  2023-01-22 08:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1   semi-ripe   
25829  2023-01-22 12:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1   semi-ripe   
25875  2023-01-22 16:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1   semi-ripe   
25934  2023-01-23 08:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1        ripe   
26014  2023-01-23 16:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1        ripe   
26061  2023-01-24 08:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1        ripe   
26087  2023-01-24 12:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1   semi-ripe   
26133  2023-01-24 16:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1   semi-ripe   
26190  2023-01-25 08:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1        ripe   
26282  2023-01-26 08:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1        ripe   
26345  2023-01-26 12:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1        ripe   
26430  2023-01-27 12:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1   semi-ripe   

      preprocessed_growth  is_ripe_to_unripe  
25783           semi-ripe                  0  
25829           semi-ripe                  0  
25875           semi-ripe                  0  
25934                ripe                  0  
26014                ripe                  0  
26061                ripe                  0  
26087           semi-ripe                  0  
26133           semi-ripe                  0  
26190                ripe                  0  
26282                ripe                  0  
26345                ripe                  0  
26430           semi-ripe                  0

In [109]:
# 마스크 id별로 순회

res_data = data.copy()

priority = {"unripe":1, "semi-ripe":2, "ripe":3}

for i, mask_id in enumerate(res_data["mask_id"].unique()):
    print(f"{i}번째 mask_id : {mask_id}")
    case = res_data[res_data["mask_id"] == mask_id]["preprocessed_growth"]
    if len(case) <= 1 : continue
    # 마지막 우선순위가 더 낮다면
    if priority[case.iloc[-2]] > priority[case.iloc[-1]]:
        print(f"{case.iloc[-2]} -> {case.iloc[-1]}")
        res_data.loc[case.index[-1], "preprocessed_growth"] = case.iloc[-2]

0번째 mask_id : 065e7a9bdd5065fe01976ff3f4f49f03_0
1번째 mask_id : c8f4ef001e5f686be96b1cb1bb68f68d_0
2번째 mask_id : 3cf79ada342fb0b16364c9ea6d703f9f_0
3번째 mask_id : 491cac2d8aeb811f039441b25b8483b0_0
4번째 mask_id : a93419f5079b7a10c49bdbefa7212931_0
5번째 mask_id : e7a51ad9cb0adeb86dbca9b32e8ae546_0
6번째 mask_id : fd48e0393a4d25876b5fb82e9571361e_0
7번째 mask_id : 3023258416cf82bfae31ce3199d34a62_0
8번째 mask_id : 66d7363516223557cf19fdbaeffd4ef1_0
9번째 mask_id : 7d78902ab2ef05dfe489937a97aa69c5_0
10번째 mask_id : 00715d5ec46b3d94a8ee5e41cf21613e_0
11번째 mask_id : 3e13eb37ab42aa111180a18790515a79_0
12번째 mask_id : 52d0cdd26abeaa1eb7d0c1dd2b02aa16_0
13번째 mask_id : b2ff0a94f4e9e1f210421f8a3275741a_0
14번째 mask_id : c6fa1a77e79158ea4befb430175636c8_0
15번째 mask_id : 57b2cac3d604c10bbfeb3e93602cbddb_0
16번째 mask_id : 6cbfc21e2b65aba2fd523ca417a174f4_0
17번째 mask_id : 68baa0aabcea125de0f2e73a970e7022_0
18번째 mask_id : e57ce9f02faa7e1128c06861f3573d09_0
19번째 mask_id : c968257436247670e60a63f2b23161f6_0
20번째 mask_

In [110]:
# 변화된 것 확인
data_check = res_data[["check_datetime", "mask_id", "pred_growth", "preprocessed_growth", "is_ripe_to_unripe"]]
data_check[data_check["mask_id"] == "f4a0c6e25664af6ed0f03228fb2c9bf3_1"]

check_datetime                             mask_id pred_growth  \
25783  2023-01-22 08:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1   semi-ripe   
25829  2023-01-22 12:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1   semi-ripe   
25875  2023-01-22 16:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1   semi-ripe   
25934  2023-01-23 08:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1        ripe   
26014  2023-01-23 16:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1        ripe   
26061  2023-01-24 08:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1        ripe   
26087  2023-01-24 12:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1   semi-ripe   
26133  2023-01-24 16:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1   semi-ripe   
26190  2023-01-25 08:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1        ripe   
26282  2023-01-26 08:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1        ripe   
26345  2023-01-26 12:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1        ripe   
26430  2023-01-27 12:40:00  f4a0c6e25664af6ed0f03228fb2c9bf3_1   semi-ripe   

      preprocessed_growth  is_ripe_to_unripe  
25783           semi-ripe                  0  
25829           semi-ripe                  0  
25875           semi-ripe                  0  
25934                ripe                  0  
26014                ripe                  0  
26061                ripe                  0  
26087           semi-ripe                  0  
26133           semi-ripe                  0  
26190                ripe                  0  
26282                ripe                  0  
26345                ripe                  0  
26430                ripe                  0

In [119]:
data_check[data_check["mask_id"] == "9d580a25bb5c5fd7a854f7ad09d3c13e_4"]

check_datetime                             mask_id pred_growth  \
10840  2022-02-25 08:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4      unripe   
10930  2022-02-25 12:50:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4      unripe   
11024  2022-02-25 16:40:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4   semi-ripe   
11112  2022-02-26 08:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4   semi-ripe   
11200  2022-02-26 12:50:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4   semi-ripe   
11289  2022-02-26 16:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4   semi-ripe   
11378  2022-02-27 08:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4   semi-ripe   
11473  2022-02-27 12:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
11575  2022-02-27 16:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
11668  2022-02-28 08:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
11776  2022-02-28 12:40:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
11874  2022-02-28 16:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
11970  2022-03-01 08:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
12075  2022-03-01 12:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
12170  2022-03-01 16:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
12266  2022-03-02 08:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
12365  2022-03-02 12:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
12467  2022-03-02 16:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
12570  2022-03-03 08:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
12658  2022-03-03 12:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   
12738  2022-03-03 16:30:00  9d580a25bb5c5fd7a854f7ad09d3c13e_4        ripe   

      preprocessed_growth  is_ripe_to_unripe  
10840              unripe                  0  
10930              unripe                  0  
11024           semi-ripe                  0  
11112           semi-ripe                  0  
11200           semi-ripe                  0  
11289           semi-ripe                  0  
11378           semi-ripe                  0  
11473                ripe                  0  
11575                ripe                  0  
11668                ripe                  0  
11776                ripe                  0  
11874                ripe                  0  
11970                ripe                  0  
12075                ripe                  0  
12170                ripe                  0  
12266                ripe                  0  
12365                ripe                  0  
12467                ripe                  0  
12570                ripe                  0  
12658                ripe                  0  
12738                ripe                  0

In [111]:
res_data.columns

Index(['Unnamed: 0.1', 'Unnamed: 0', 'check_datetime', '측정일자', '구역명',
       'farm_code', '내부온도', '내부습도', '내부CO2', '근권온도', '내부순간일사량', '측정년도', '측정월',
       'input_image_name', 'input_image_path', 'img_id', 'area_code',
       'shot_datetime', 'count_masks', 'bbox_image_path', 'before_img_name',
       'before_img_id', 'mask_num', 'mask_id', 'point_x', 'point_y', 'size',
       'color', 'output_image_path', 'origin_r', 'origin_g', 'origin_b',
       'pred_growth', 'mask_count', 'is_filtering', 'preprocessed_growth',
       'is_ripe_to_unripe'],
      dtype='object')

In [112]:
res_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 127857 entries, 0 to 127856
Data columns (total 37 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   Unnamed: 0.1         127857 non-null  int64  
 1   Unnamed: 0           127857 non-null  int64  
 2   check_datetime       127857 non-null  object 
 3   측정일자                 127857 non-null  object 
 4   구역명                  127857 non-null  object 
 5   farm_code            127857 non-null  object 
 6   내부온도                 126222 non-null  float64
 7   내부습도                 126222 non-null  float64
 8   내부CO2                126222 non-null  float64
 9   근권온도                 126222 non-null  float64
 10  내부순간일사량              126222 non-null  float64
 11  측정년도                 127857 non-null  int64  
 12  측정월                  127857 non-null  int64  
 13  input_image_name     127857 non-null  object 
 14  input_image_path     127857 non-null  object 
 15  img_id           

저장 전 컬럼 처리
- is_ripe_to_unripe 삭제
- pred_growth 삭제 후 preprocessed_growth를 pred_growth로 rename

In [113]:
res_data.drop(["is_ripe_to_unripe", "pred_growth"], axis=1, inplace=True)

In [114]:
res_data.rename(columns={"preprocessed_growth":"pred_growth"}, inplace=True)

In [115]:
# 실수로 생긴 컬럼 삭제
res_data.drop(['Unnamed: 0.1', 'Unnamed: 0'], axis=1, inplace=True)

In [116]:
res_data.columns

Index(['check_datetime', '측정일자', '구역명', 'farm_code', '내부온도', '내부습도', '내부CO2',
       '근권온도', '내부순간일사량', '측정년도', '측정월', 'input_image_name',
       'input_image_path', 'img_id', 'area_code', 'shot_datetime',
       'count_masks', 'bbox_image_path', 'before_img_name', 'before_img_id',
       'mask_num', 'mask_id', 'point_x', 'point_y', 'size', 'color',
       'output_image_path', 'origin_r', 'origin_g', 'origin_b', 'mask_count',
       'is_filtering', 'pred_growth'],
      dtype='object')

In [121]:
# 저장
res_data.sort_values(by=["farm_code", "check_datetime"], inplace=True)
res_data.to_csv("merge_drowth_real_final_filtering_final.csv", encoding="utf8", index=False)

In [126]:
import pandas as pd
data = pd.read_csv("growth_preprocessed_filtering_data.csv")

In [127]:
from datetime import datetime 

def period(start_date, end_date):
    start_date = datetime.strptime(start_date,'%Y-%m-%d %H:%M:%S')
    end_date = datetime.strptime(end_date, '%Y-%m-%d %H:%M:%S')
    return (start_date, end_date)


period_22_23 = period('2022-08-25 16:44:07', '2023-06-23 16:36:06')


# 농가별로 작기별 데이터를 만들어서 재저장
data['check_datetime'] = pd.to_datetime(data['check_datetime'])
data_period_22_23 = data[(data['check_datetime'] >= period_22_23[0]) & (data['check_datetime'] <= period_22_23[1])]


In [139]:
F0016_period_22_23 = data_period_22_23[data_period_22_23["farm_code"]=="F0016"]

In [136]:
data_period_22_23.shape

(42044, 35)

In [140]:
F0016_22_23_nov = F0016_period_22_23[(F0016_period_22_23['check_datetime'].dt.month == 11) & (F0016_period_22_23['check_datetime'].dt.year == 2022)]

In [141]:
F0016_22_23_nov[F0016_22_23_nov["mask_id"].str.contains("3a6fa38ba0cb20538b782ccac4b90eb2_7")]

check_datetime        측정일자  구역명 farm_code   내부온도   내부습도  내부CO2  \
23754 2022-11-08 12:40:00  2022-11-08  1구역     F0016  23.64  71.21  435.2   
23763 2022-11-08 16:40:00  2022-11-08  1구역     F0016  19.51  61.30  461.9   
23780 2022-11-09 08:40:00  2022-11-09  1구역     F0016  14.99  94.44  599.3   
23799 2022-11-09 12:40:00  2022-11-09  1구역     F0016  22.02  72.87  456.2   
23810 2022-11-09 16:40:00  2022-11-09  1구역     F0016  17.67  76.04  436.9   
23837 2022-11-10 08:40:00  2022-11-10  1구역     F0016  15.02  86.73  778.3   
23858 2022-11-10 12:40:00  2022-11-10  1구역     F0016  23.48  59.88  461.9   
23865 2022-11-10 16:40:00  2022-11-10  1구역     F0016  20.87  57.74  474.2   

        근권온도  내부순간일사량  측정년도  ...  \
23754  15.24   445.18  2022  ...   
23763  17.39    61.22  2022  ...   
23780  16.01    66.39  2022  ...   
23799  16.39   381.87  2022  ...   
23810  17.68    35.78  2022  ...   
23837  14.84   144.32  2022  ...   
23858  15.33   344.25  2022  ...   
23865  17.16    76.53  2022  ...   

                                                   color output_image_path  \
23754  [[100, 107, 117], [85, 92, 102], [90, 97, 107]...  image_mask_2.png   
23763  [[76, 76, 76], [79, 79, 79], [78, 78, 78], [73...  image_mask_6.png   
23780  [[76, 72, 69], [65, 66, 61], [68, 69, 64], [73...  image_mask_8.png   
23799  [[79, 86, 94], [79, 86, 94], [79, 86, 94], [79...  image_mask_2.png   
23810  [[90, 92, 91], [89, 91, 90], [89, 91, 90], [89...  image_mask_7.png   
23837  [[66, 62, 25], [57, 53, 16], [108, 104, 67], [...  image_mask_9.png   
23858  [[66, 69, 78], [66, 69, 78], [66, 69, 78], [66...  image_mask_3.png   
23865  [[74, 79, 82], [76, 81, 84], [78, 83, 86], [80...  image_mask_6.png   

       origin_r  origin_g  origin_b mask_count  is_filtering pred_growth  \
23754  0.327758  0.327074  0.345168        9.0           0.0      unripe   
23763  0.348186  0.325902  0.325912       14.0           0.0   semi-ripe   
23780  0.414784  0.302073  0.283143       25.0           0.0        ripe   
23799  0.335006  0.320637  0.344357        7.0           0.0      unripe   
23810  0.397293  0.304218  0.298489       23.0           0.0   semi-ripe   
23837  0.439968  0.295960  0.264073       31.0           0.0   semi-ripe   
23858  0.346688  0.311752  0.341559        6.0           0.0   semi-ripe   
23865  0.372802  0.303714  0.323484       14.0           0.0   semi-ripe   

      unripe_to_semi-ripe semi-ripe_to_ripe  
23754                 1.0               1.0  
23763                 1.0               1.0  
23780                 1.0               1.0  
23799                 1.0               NaN  
23810                 1.0               NaN  
23837                 1.0               NaN  
23858                 1.0               NaN  
23865                 1.0               NaN  

[8 rows x 35 columns]

In [134]:
data_period_22_23[data_period_22_23["mask_id"].str.contains("3a6fa38ba0cb20538b782ccac4b90eb2_7")]

check_datetime        측정일자  구역명 farm_code   내부온도   내부습도  내부CO2  \
23754 2022-11-08 12:40:00  2022-11-08  1구역     F0016  23.64  71.21  435.2   
23763 2022-11-08 16:40:00  2022-11-08  1구역     F0016  19.51  61.30  461.9   
23780 2022-11-09 08:40:00  2022-11-09  1구역     F0016  14.99  94.44  599.3   
23799 2022-11-09 12:40:00  2022-11-09  1구역     F0016  22.02  72.87  456.2   
23810 2022-11-09 16:40:00  2022-11-09  1구역     F0016  17.67  76.04  436.9   
23837 2022-11-10 08:40:00  2022-11-10  1구역     F0016  15.02  86.73  778.3   
23858 2022-11-10 12:40:00  2022-11-10  1구역     F0016  23.48  59.88  461.9   
23865 2022-11-10 16:40:00  2022-11-10  1구역     F0016  20.87  57.74  474.2   

        근권온도  내부순간일사량  측정년도  ...  \
23754  15.24   445.18  2022  ...   
23763  17.39    61.22  2022  ...   
23780  16.01    66.39  2022  ...   
23799  16.39   381.87  2022  ...   
23810  17.68    35.78  2022  ...   
23837  14.84   144.32  2022  ...   
23858  15.33   344.25  2022  ...   
23865  17.16    76.53  2022  ...   

                                                   color output_image_path  \
23754  [[100, 107, 117], [85, 92, 102], [90, 97, 107]...  image_mask_2.png   
23763  [[76, 76, 76], [79, 79, 79], [78, 78, 78], [73...  image_mask_6.png   
23780  [[76, 72, 69], [65, 66, 61], [68, 69, 64], [73...  image_mask_8.png   
23799  [[79, 86, 94], [79, 86, 94], [79, 86, 94], [79...  image_mask_2.png   
23810  [[90, 92, 91], [89, 91, 90], [89, 91, 90], [89...  image_mask_7.png   
23837  [[66, 62, 25], [57, 53, 16], [108, 104, 67], [...  image_mask_9.png   
23858  [[66, 69, 78], [66, 69, 78], [66, 69, 78], [66...  image_mask_3.png   
23865  [[74, 79, 82], [76, 81, 84], [78, 83, 86], [80...  image_mask_6.png   

       origin_r  origin_g  origin_b mask_count  is_filtering pred_growth  \
23754  0.327758  0.327074  0.345168        9.0           0.0      unripe   
23763  0.348186  0.325902  0.325912       14.0           0.0   semi-ripe   
23780  0.414784  0.302073  0.283143       25.0           0.0        ripe   
23799  0.335006  0.320637  0.344357        7.0           0.0      unripe   
23810  0.397293  0.304218  0.298489       23.0           0.0   semi-ripe   
23837  0.439968  0.295960  0.264073       31.0           0.0   semi-ripe   
23858  0.346688  0.311752  0.341559        6.0           0.0   semi-ripe   
23865  0.372802  0.303714  0.323484       14.0           0.0   semi-ripe   

      unripe_to_semi-ripe semi-ripe_to_ripe  
23754                 1.0               1.0  
23763                 1.0               1.0  
23780                 1.0               1.0  
23799                 1.0               NaN  
23810                 1.0               NaN  
23837                 1.0               NaN  
23858                 1.0               NaN  
23865                 1.0               NaN  

[8 rows x 35 columns]

In [129]:
for mask_id in data_period_22_23["mask_id"].unique():
    if len(mask_id.split("_")) > 1:
        print(mask_id)

153e248144493bd1556e83418b31eee9_1
710f5d17cc5f14b0e0f14f897396c40e_9
b28f6ddf90b883f012a2416ce882e50d_2
698ef0c1d268bf4a8603f59f40148a00_7
698ef0c1d268bf4a8603f59f40148a00_8
db7e0333f7d3b3b07365e45e42813657_0
0a058b360c11de89f41f7d66a8cf7f3d_3
d31a3a7509f74eef21ca039cc14b16f5_7
42a267e861f209daecb0d94faf32c1b6_4
a2032b15160e3f1e779628bd97691aa1_3
b28f6ddf90b883f012a2416ce882e50d_3
710f5d17cc5f14b0e0f14f897396c40e_10
49f8a997238a9745cd079d25ab3e08cd_1
5cdc36596028ee2e0ca6042f208f01a3_2
350975a5765500509b9329b3685e9f63_6
d31a3a7509f74eef21ca039cc14b16f5_8
626d432a9ce347fae736971bc10669c7_8
2bfa6e354738cfc22656e6518778fd49_0
2bfa6e354738cfc22656e6518778fd49_1
3c6562b90af5d489b2fbd43e8d18e5b7_0
59e8169cf1c4b838c28fa01e8da9e88e_3
855281010e668aaaca9efbf764bdccbf_5
95205b1c3163df014549fc82d8530050_2
0f08f8f47dbfcaedcc52e95b083251ed_2
9deda7aea5f8b03a7488466ff5766d0f_3
067a480b75ed924d81d916362997bbfa_5
18cfad18dea9b61c338ee9bb5f68f7bc_1
855281010e668aaaca9efbf764bdccbf_5_0
8131e97ca78a111d8